In [3]:
import os
import pandas as pd
import numpy as np
import datetime as dt
from pandas_profiling import ProfileReport


#setting up a file dir so I can reuse it
#file_dir = 'C:\Users\baffo\Desktop\novelis_take_home\take_home_docs\'
os.chdir('C:\\Users\\baffo\\Desktop\\novelis_take_home\\take_home_docs\\')


#reading in the data for EDA
user_trans =  pd.read_csv('Candidate_tech_evaluation_candidate_copy_data_science_fraud.csv')

ip_to_country_map = pd.read_excel('Candidate_tech_evaluation_candidate_copy_datascience_IpAddress_to_Country.xlsx')

print('Diemnsions of user transaction is: {0} \nDimensions of IP address to country mapping is: {1}'.format(user_trans.shape, ip_to_country_map.shape))


Diemnsions of user transaction is: (120000, 11) 
Dimensions of IP address to country mapping is: (138846, 3)


## Initial exploration to understand data includes the following question
1. Are there duplicate rows in the user trans data       
2. Is the data truly unique at customer ID level
3. Is device ID unique or it can be shared
4. Is IP address unique
5. Does the join to map each ip address to its corresponding country results in duplicate rows being created or attribution to multiple countries

### Are there duplicate rows

In [4]:
#As seen in the output below, the data does not have duplicates
print('Dimensions of user transactions before dropping duplicates is: {0} \nDimension of user transactions after dropping duplicates is: {1}'.format(user_trans.shape, user_trans.drop_duplicates().shape))

Dimensions of user transactions before dropping duplicates is: (120000, 11) 
Dimension of user transactions after dropping duplicates is: (120000, 11)


### Is the data truly unique at customer ID level

In [5]:
#As seen in the output below, the number of unique user_id is equal to the number of rows in the user trans table
print('number of unique user_id is {}'.format(user_trans[['user_id']].drop_duplicates().size))

number of unique user_id is 120000


### Is device ID unique or it can be shared

In [6]:
#As seen in the output below, there are some devices that were share by different user
# If I had data on the first time a given device was used, I would have created a feature about if the device id has been used in a fraudulent activity
print('number of unique devices is {}'.format(user_trans[['device_id']].drop_duplicates().size))

number of unique devices is 110599


### Is IP address unique

In [7]:
#IP address is not unique as well
# Same idea as device id, a feature could have been created on this field to capture whether the ip address has been used in a fraudulent activity before
print('number of unique devices is {}'.format(user_trans[['ip_address']].drop_duplicates().size))

number of unique devices is 114134


### Does the join to map each ip address to its corresponding country results in duplicate rows being created or attribution to multiple countries
* My compute resource could now handle the cross join between the user trans table and the ip address to country mapping  table. 
* Looping chunking the operation up by looping over individual countries and it did not work
* I will table this as something I can do as next step as bring this data to compute on my local machine is very expensive.
* The cell below shows how I was creating the Ip to country map

###  Do not run the next cell!

In [ ]:
# Get a list of unique countries to loop over it
countries = list(ip_to_country_map.country.unique())

results = []
i = 1
total_iter = len(countries)
ip_table = 
for country in countries:
    
    print('iteration {0} of {1}'.format(i, total_iter))
    
    #subset the country map df to include only one country and do the cross join
    country_df = ip_to_country_map[ip_to_country_map['country'] == country]
    
    tmp_cross_join = ip_table.merge(country_df, how = 'cross')
    tmp_cross_join =  tmp_cross_join[(tmp_cross_join.ip_address >= tmp_cross_join.lower_bound_ip_address) & (tmp_cross_join.ip_address <= tmp_cross_join.upper_bound_ip_address)]
    
    # Store the cross join as a list of dict and append it to the master list initialized above
    # Before converting to list of dict, I want to make sure I am dropping duplicates
    tmp = tmp_cross_join[['ip_address', 'country']].drop_duplicates().to_dict('records')
    results.append(tmp)
    
    i += 1
    
# convert the list of dict bact to Dataframe
ip_look_up = pd.DataFrame.from_dict(results)


### Feature engineering and Exploratory Data Analysis
In this session, the following needs to be done in order to fully understand the data and fit the model
1. Check the dtypes of the columns
2. Engineer the following variable from signup and purchase times
    * Day, hour, month of both signup and purchase time
    * Number of Days, Hours, Minutes between signup and purchase time
3. Explore the data

### Check the dtypes of the columns

In [8]:
user_trans.dtypes

user_id             int64
signup_time        object
purchase_time      object
purchase_value      int64
device_id          object
source             object
browser            object
sex                object
age                 int64
ip_address        float64
class               int64
dtype: object

### Engineer features from signup and purchase times

In [9]:
user_trans['signup_time_dt'] = pd.to_datetime(user_trans['signup_time'], format = '%m/%d/%y %H:%M')
user_trans['signup_year'] = pd.DatetimeIndex(user_trans['signup_time_dt']).year
user_trans['signup_month'] = user_trans[['signup_time_dt']].apply(lambda x: dt.datetime.strftime(x['signup_time_dt'], '%B'), axis=1)
user_trans['signup_day'] = user_trans[['signup_time_dt']].apply(lambda x: dt.datetime.strftime(x['signup_time_dt'], '%A'), axis=1)
user_trans['signup_hour'] = pd.DatetimeIndex(user_trans['signup_time_dt']).hour


user_trans['purchase_time_dt'] = pd.to_datetime(user_trans['purchase_time'], format = '%m/%d/%y %H:%M')
user_trans['purchase_year'] = pd.DatetimeIndex(user_trans['purchase_time_dt']).year
user_trans['purchase_month'] = user_trans[['purchase_time_dt']].apply(lambda x: dt.datetime.strftime(x['purchase_time_dt'], '%B'), axis=1)
user_trans['purchase_day'] = user_trans[['purchase_time_dt']].apply(lambda x: dt.datetime.strftime(x['purchase_time_dt'], '%A'), axis=1)
user_trans['purchase_hour'] = pd.DatetimeIndex(user_trans['purchase_time_dt']).hour

user_trans['time_delta_signup_purchase'] = user_trans['purchase_time_dt'] - user_trans['signup_time_dt']
user_trans['time_delta_secs'] = user_trans[['time_delta_signup_purchase']].applymap(lambda x: x.total_seconds())
user_trans['time_delta_mins'] = user_trans[['time_delta_secs']].applymap(lambda x: divmod(x, 60)[0])
user_trans['time_delta_hours'] = user_trans[['time_delta_secs']].applymap(lambda x: divmod(x, 3600)[0])
user_trans['time_delta_days'] = user_trans[['time_delta_secs']].applymap(lambda x: divmod(x, 86400)[0])

user_trans[['time_delta_signup_purchase', 'time_delta_secs','time_delta_mins', 'time_delta_hours', 'time_delta_days']].head()

time_delta_signup_purchase  time_delta_secs  time_delta_mins  \
0           57 days 09:41:00        4959660.0          82661.0   
1           78 days 16:24:00        6798240.0         113304.0   
2           25 days 11:29:00        2201340.0          36689.0   
3            1 days 20:53:00         161580.0           2693.0   
4           59 days 17:15:00        5159700.0          85995.0   

   time_delta_hours  time_delta_days  
0            1377.0             57.0  
1            1888.0             78.0  
2             611.0             25.0  
3              44.0              1.0  
4            1433.0             59.0

In [10]:
profile = ProfileReport(user_trans[['purchase_value', 'source', 'browser', 'sex', 'age', 'class', 'signup_year', 'signup_month', 'signup_day', 'signup_hour',
                                   'purchase_year', 'purchase_month', 'purchase_day', 'purchase_hour', 'time_delta_secs', 'time_delta_mins', 'time_delta_hours', 'time_delta_days']], title="Pandas Profiling Report")
profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

### Model fitting
The following observaation will inform the next steps to model fitting
1. Since the data is 2015 data, I will drop the engineered year features
2. I will only keep the number of seconds of the sign-up to purchase timeframe
3. I will convert the low cardinality categorical variable to dummy encoded variables and throw away the high cardinality ones like device_id
4. Since I was unable to map the ip address to countries, I will drop it together because of its high cardinality

### Class imbalance aparent
Looking at the distribution of the class variable, it is clear that there is a class imbalance issue with this data. I will fit my base line model without any class imbalance mitigation. However, the challenger models will include both over sampling of the minority class (Giving more data, I will try under-sampling in future iteration)

### Types of models that will be fitted
Due to time constraint, I will only experiment 3 model (GBM, Random forest and Logistic regression).

In [11]:
# Before splitting the data, I will derive the dummies for the categorical variables
dummies = pd.get_dummies(data = user_trans[['source', 'browser', 'sex', 'signup_month', 'signup_day', 
                                   'purchase_month', 'purchase_day']], prefix= ['source', 'browser','sex', 'sm', 'sd', 'pm', 'pd'], drop_first=True)

#resetting index as pd.concat was acting up without the index reset
dummies.reset_index(drop=True, inplace=True)
user_trans.reset_index(drop=True, inplace=True)

user_trans_with_dummies = pd.concat([user_trans, dummies], axis = 1)
user_trans_with_dummies.head()

user_id    signup_time  purchase_time  purchase_value      device_id  \
0   285108   7/15/15 4:36  9/10/15 14:17              31  HZAKVUFTDOSFD   
1   131009  1/24/15 12:29   4/13/15 4:53              31  XGQAJSOUJIZCC   
2   328855   3/11/15 0:54   4/5/15 12:23              16  VCCTAYDCWKZIY   
3   229053   1/7/15 13:19   1/9/15 10:12              29  MFFIHYNXCJLEY   
4   108439   2/8/15 21:11   4/9/15 14:26              26  WMSXWGVPNIFBM   

   source  browser sex  age    ip_address  ...  pm_May pm_November  \
0  Direct   Chrome   M   49  2.818400e+09  ...       0           0   
1     SEO       IE   F   21  3.251268e+09  ...       0           0   
2  Direct       IE   M   26  2.727760e+09  ...       0           0   
3     SEO   Chrome   M   34  2.083420e+09  ...       0           0   
4     Ads  FireFox   M   33  3.207913e+09  ...       0           0   

   pm_October pm_September pd_Monday  pd_Saturday pd_Sunday  pd_Thursday  \
0           0            1         0            0         0            1   
1           0            0         1            0         0            0   
2           0            0         0            0         1            0   
3           0            0         0            0         0            0   
4           0            0         0            0         0            1   

  pd_Tuesday pd_Wednesday  
0          0            0  
1          0            0  
2          0            0  
3          0            0  
4          0            0  

[5 rows x 63 columns]

In [12]:
from sklearn.model_selection import train_test_split
from sklearn.ensemble import GradientBoostingClassifier, RandomForestClassifier
from sklearn.linear_model import LogisticRegression
import statsmodels.api as sm

 
#splitting the data 
cols_for_model = ['purchase_value','age', 'time_delta_secs'] + list(dummies)
x = user_trans_with_dummies[cols_for_model]
y = user_trans_with_dummies['class']

X_train, X_test, y_train, y_test = train_test_split(x, y, test_size=0.2, random_state=1)

X_train, X_val, y_train, y_val = train_test_split(X_train, y_train, test_size=0.25, random_state=1) 
 
# Base model fitting with stats model logistic regression to see the the coefficient of each feature before going to accuracy measures
# I like this better than the feature importance derived from shuffling features around in non parametric approaches
log_reg = sm.Logit(y_train, X_train).fit()
print(log_reg.summary())

Optimization terminated successfully.
         Current function value: 0.214355
         Iterations 7
                           Logit Regression Results                           
Dep. Variable:                  class   No. Observations:                72000
Model:                          Logit   Df Residuals:                    71960
Method:                           MLE   Df Model:                           39
Date:                Mon, 17 Jan 2022   Pseudo R-squ.:                  0.3132
Time:                        16:24:49   Log-Likelihood:                -15434.
converged:                       True   LL-Null:                       -22472.
Covariance Type:            nonrobust   LLR p-value:                     0.000
                      coef    std err          z      P>|z|      [0.025      0.975]
-----------------------------------------------------------------------------------
purchase_value     -0.0043      0.001     -5.086      0.000      -0.006      -0.003
age           

In [13]:
from sklearn.metrics import classification_report, roc_auc_score, confusion_matrix


# Looks like a good subset of the features were significant in predicting fraud
# Below I measure the accracy metrics on the validation set
logisticRegr = LogisticRegression()
logisticRegr.fit(X_train, y_train)
y_pred = logisticRegr.predict(X_val)
y_proba = logisticRegr.predict_proba(X_val)[:, 1]

target_names = ['class 0', 'class 1']
print(classification_report(y_val, y_pred, target_names = target_names))
print(roc_auc_score(y_val, y_proba))

print(confusion_matrix(y_val, y_pred))

              precision    recall  f1-score   support

     class 0       0.91      1.00      0.95     21772
     class 1       0.00      0.00      0.00      2228

    accuracy                           0.91     24000
   macro avg       0.45      0.50      0.48     24000
weighted avg       0.82      0.91      0.86     24000

0.767308541334694
[[21772     0]
 [ 2228     0]]


C:\Users\baffo\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\baffo\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\baffo\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


As seen from the output above, the base model seem to be predicting every transaction as legitimate. This may be due class imbalance.
I will upsample the minority class in the training set and refit the base model again

In [14]:
from imblearn.over_sampling import RandomOverSampler

# define oversampling strategy
oversample = RandomOverSampler(sampling_strategy='minority')
X_over, y_over = oversample.fit_resample(X_train, y_train)


logisticRegr = LogisticRegression()
logisticRegr.fit(X_over, y_over)
y_pred = logisticRegr.predict(X_val)
y_proba = logisticRegr.predict_proba(X_val)[:, 1]

target_names = ['class 0', 'class 1']
print(classification_report(y_val, y_pred, target_names = target_names))
print(roc_auc_score(y_val, y_proba))

print(confusion_matrix(y_val, y_pred))

              precision    recall  f1-score   support

     class 0       0.95      1.00      0.98     21772
     class 1       1.00      0.53      0.69      2228

    accuracy                           0.96     24000
   macro avg       0.98      0.77      0.84     24000
weighted avg       0.96      0.96      0.95     24000

0.7673088917922348
[[21772     0]
 [ 1044  1184]]


Regular oversampling seemed to help mitigate the issue with predicting every transaction to be legitimate.
We see see the the precision  with which we predicted fraudulent transactions was 100% and that of legitimate transactions was 95% and this is better than the previous model

Below is another variation of over sampling before I move on to the challenger models

In [16]:
from imblearn.over_sampling import SMOTE

oversample_smote = SMOTE()
X_over, y_over = oversample_smote.fit_resample(X_train, y_train)

logisticRegr = LogisticRegression()
logisticRegr.fit(X_over, y_over)
y_pred = logisticRegr.predict(X_val)
y_proba = logisticRegr.predict_proba(X_val)[:, 1]

target_names = ['class 0', 'class 1']
print(classification_report(y_val, y_pred, target_names = target_names))
print(roc_auc_score(y_val, y_proba))

print(confusion_matrix(y_val, y_pred))

              precision    recall  f1-score   support

     class 0       0.95      1.00      0.98     21772
     class 1       1.00      0.53      0.69      2228

    accuracy                           0.96     24000
   macro avg       0.98      0.77      0.84     24000
weighted avg       0.96      0.96      0.95     24000

0.7673088917922348
[[21772     0]
 [ 1044  1184]]


Since smote did not add any incremental benefit to the accuracy metrics I will chooe the regular over sampling as my baseline model.

## Challenger models
### GBM

In [21]:
#regular over sampling
oversample = RandomOverSampler(sampling_strategy='minority')
X_over, y_over = oversample.fit_resample(X_train, y_train)

# from sklearn.model_selection import RepeatedStratifiedKFold
# from sklearn.model_selection import GridSearchCV

model_gbm = GradientBoostingClassifier()
model_rf = RandomForestClassifier()

model_gbm.fit(X_over, y_over)
y_pred_gbm = model_gbm.predict(X_val)
y_proba_gbm = model_gbm.predict_proba(X_val)[:, 1]

target_names = ['class 0', 'class 1']
print(classification_report(y_val, y_pred_gbm, target_names = target_names))
print(roc_auc_score(y_val, y_proba_gbm))


              precision    recall  f1-score   support

     class 0       0.95      1.00      0.98     21772
     class 1       1.00      0.54      0.70      2228

    accuracy                           0.96     24000
   macro avg       0.98      0.77      0.84     24000
weighted avg       0.96      0.96      0.95     24000

0.7778398213606592


### Random forest

In [22]:
model_rf = RandomForestClassifier()

model_rf.fit(X_over, y_over)
y_pred_rf = model_rf.predict(X_val)
y_proba_rf = model_rf.predict_proba(X_val)[:, 1]

target_names = ['class 0', 'class 1']
print(classification_report(y_val, y_pred_rf, target_names = target_names))
print(roc_auc_score(y_val, y_proba_rf))


              precision    recall  f1-score   support

     class 0       0.95      1.00      0.98     21772
     class 1       0.97      0.54      0.69      2228

    accuracy                           0.96     24000
   macro avg       0.96      0.77      0.83     24000
weighted avg       0.96      0.96      0.95     24000

0.774817259069099


### Winning model
Winning model is based on precision, recall and auc Gradient boosting Classifier

## Next steps
Unfortunately, I could not finish this within the alloted time (had a family emergency over the weekend) and just so I demonstrate my model fitting acumen, I wanted to articulate the next steps I will take if I had additional time
1. Experiemnts with other models like xgboost, svm etc
2. Also experiement with undersampling
3. Do hyperparameter tuning using grid search
4. Additional feature engineering will revolve around whether fraud has been reported on IP address and devices
5. If I can get the ip address to country mapping to work, I will also add originating country as a feature
6. Run some machine learning intepretability methods on the winning model to understand what raises the risk factor of a given transaction to come up with additional set of feature engineering
7. Modularize the feature engineering and preprocessing with a function for easing scoring of the hold out set